In [101]:
#vamos a probar modelos de ML
#leamos x_train, y_train, x_test, y_test
import pandas as pd
x_train = pd.read_csv("x_train.csv")
y_train = pd.read_csv("y_train.csv")
x_test = pd.read_csv("x_val.csv")
y_test = pd.read_csv("y_val.csv")




In [88]:
# ==============================
# Optuna + Pruning para LGBM
# ==============================
import numpy as np
import pandas as pd
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from lightgbm import LGBMRegressor
import optuna
from optuna.samplers import TPESampler
from optuna.pruners import MedianPruner
from optuna.integration import LightGBMPruningCallback

SEED = 42
VAL_FRAC = 0.20   # último 20% del train como validación temporal
N_TRIALS = 50     # ajustá según tiempo disponible

# --------- Split temporal (train -> train/valid ; test queda intacto) ---------
X_train_all = x_train.copy()
y_train_all = y_train.copy()
X_test = x_test.copy()
y_test = y_test.copy()

n = len(X_train_all)
n_val = int(np.floor(n * VAL_FRAC))
n_tr = n - n_val
X_tr, y_tr = X_train_all.iloc[:n_tr], y_train_all[:n_tr]
X_val, y_val = X_train_all.iloc[n_tr:], y_train_all[n_tr:]

print(f"Train: {X_tr.shape}, Valid: {X_val.shape}, Test: {X_test.shape}")

# --------- Función objetivo para Optuna ---------
def objective(trial: optuna.Trial) -> float:
    # Espacio de búsqueda (razonable para baseline)
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 300, 2000),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.2, log=True),
        "num_leaves": trial.suggest_int("num_leaves", 31, 255),
        "max_depth": trial.suggest_int("max_depth", -1, 16),
        "min_child_samples": trial.suggest_int("min_child_samples", 5, 100),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),
        "reg_alpha": trial.suggest_float("reg_alpha", 1e-8, 10.0, log=True),
        "reg_lambda": trial.suggest_float("reg_lambda", 1e-8, 10.0, log=True),
        "random_state": SEED,
        "n_jobs": -1
    }

    # Modelo
    model = LGBMRegressor(**params)

    # Pruning callback: monitorea 'rmse' en el primer eval_set (valid_0)
    pruning_cb = LightGBMPruningCallback(trial, metric="rmse", valid_name="valid_0")

    # Entrena con early stopping y pruning
    model.fit(
        X_tr, y_tr,
        eval_set=[(X_val, y_val)],
        eval_metric="rmse",
        callbacks=[pruning_cb],
    )

    # Predicción en valid y métrica a minimizar (RMSE)
    y_pred_val = model.predict(X_val)
    rmse_val = mean_squared_error(y_val, y_pred_val)
    return rmse_val

# --------- Estudio Optuna ---------
study = optuna.create_study(
    direction="minimize",
    sampler=TPESampler(seed=SEED),
    pruner=MedianPruner(n_warmup_steps=10)
)
study.optimize(objective, n_trials=N_TRIALS, show_progress_bar=True)

print("\n=== Mejores hiperparámetros ===")
print(study.best_params)
print(f"Mejor RMSE valid: {study.best_value:.4f}")

# --------- Re-entrenar con los mejores params (train+valid) ---------
best_params = study.best_params.copy()
best_model = LGBMRegressor(**best_params, random_state=SEED, n_jobs=-1)

best_model.fit(
    X_train_all, y_train_all,
    eval_set=[(X_val, y_val)],  # opcional, solo para logging
    eval_metric="rmse",
)

# --------- Evaluación en TEST ---------
y_pred_test = best_model.predict(X_test)
mse = mean_squared_error(y_test, y_pred_test)
rmse = mean_squared_error(y_test, y_pred_test)
mae = mean_absolute_error(y_test, y_pred_test)
r2  = r2_score(y_test, y_pred_test)

print("\n=== Métricas en TEST ===")
print(f"MSE : {mse:,.2f}")
print(f"RMSE: {rmse:,.2f}")
print(f"MAE : {mae:,.2f}")
print(f"R²  : {r2:.4f}")


[I 2025-11-10 00:17:21,722] A new study created in memory with name: no-name-806e30fa-e537-4897-9e0c-c902f55581ee


Train: (692, 140), Valid: (172, 140), Test: (94, 140)


  0%|          | 0/50 [00:00<?, ?it/s]

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002544 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 30310
[LightGBM] [Info] Number of data points in the train set: 692, number of used features: 140
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 28710.196171
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with 

Best trial: 0. Best value: 2.60139e+09:   2%|▏         | 1/50 [00:00<00:39,  1.24it/s]

...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

Best trial: 40. Best value: 8.83178e+07:  98%|█████████▊| 49/50 [00:29<00:00,  1.07it/s]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

Best trial: 40. Best value: 8.83178e+07: 100%|██████████| 50/50 [00:29<00:00,  1.69it/s]


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[I 2025-11-10 00:17:51,341] Trial 49 pruned. Trial was pruned at iteration 10.

=== Mejores hiperparámetros ===
{'n_estimators': 719, 'learning_rate': 0.051028986261133925, 'num_leaves': 166, 'max_depth': 7, 'min_child_samples': 13, 'subsample': 0.6622888045212691, 'colsample_bytree': 0.8189257141968503, 'reg_alpha': 6.848208783295387e-06, 'reg_lambda': 1.1919148850901538e-06}
Mejor RMSE valid: 88317810.7150
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002298 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 34198
[LightGBM] [Info] Number of data points in the train set: 864, number of used features: 140
[LightGBM] [Warning] Found whitespace in feature_names, replace with 

In [38]:
# ==============================
# Optuna para RandomForestRegressor (split temporal) + "pruning" pasivo
# ==============================
import numpy as np
import pandas as pd
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from sklearn.ensemble import RandomForestRegressor
import optuna
from optuna.samplers import TPESampler
from optuna.pruners import MedianPruner

SEED = 42
VAL_FRAC = 0.20    # último 20% del train como valid
N_TRIALS = 60      # subí/bajá según tiempo

# --------- Split temporal (train -> train/valid ; test queda intacto) ---------
X_train_all = x_train.copy()
y_train_all = y_train.copy()
X_test = x_test.copy()
y_test = y_test.copy()

n = len(X_train_all)
n_val = int(np.floor(n * VAL_FRAC))
n_tr = n - n_val
X_tr, y_tr = X_train_all.iloc[:n_tr], y_train_all[:n_tr]
X_val, y_val = X_train_all.iloc[n_tr:], y_train_all[n_tr:]

print(f"Train: {X_tr.shape}, Valid: {X_val.shape}, Test: {X_test.shape}")

# --------- Función objetivo ---------
def objective(trial: optuna.Trial) -> float:
    # Espacio de búsqueda (robusto para RF sklearn)
    max_depth_choice = trial.suggest_categorical("max_depth", [None, 6, 10, 16, 24, 32])
    max_features_choice = trial.suggest_categorical("max_features", ["sqrt", "log2", 0.5, 0.7, 1.0])
    bootstrap_choice = trial.suggest_categorical("bootstrap", [True, False])

    params = {
        "n_estimators": trial.suggest_int("n_estimators", 200, 2000),
        "criterion": "squared_error",
        "max_depth": max_depth_choice,                 # None = sin límite
        "min_samples_split": trial.suggest_int("min_samples_split", 2, 20),
        "min_samples_leaf": trial.suggest_int("min_samples_leaf", 1, 20),
        "max_features": max_features_choice,           # fracción o estrategia
        "bootstrap": bootstrap_choice,
        "random_state": SEED,
        "n_jobs": -1,
    }

    # Si se usa bootstrap, probar muestreo parcial de filas
    if bootstrap_choice:
        params["max_samples"] = trial.suggest_float("max_samples", 0.5, 1.0)

    # Modelo
    model = RandomForestRegressor(**params)

    # Entrenar y evaluar en VALID (métrica a minimizar: RMSE)
    model.fit(X_tr, y_tr)
    y_pred_val = model.predict(X_val)
    rmse_val = mean_squared_error(y_val, y_pred_val)

    # Registrar también como “valor intermedio” (no habrá pruning real, pero queda logueado)
    trial.report(rmse_val, step=0)
    # if trial.should_prune():   # en RF no habrá pasos intermedios útiles
    #     raise optuna.exceptions.TrialPruned()

    return rmse_val

# --------- Estudio Optuna ---------
study = optuna.create_study(
    direction="minimize",
    sampler=TPESampler(seed=SEED),
    pruner=MedianPruner(n_warmup_steps=5)  # no tendrá efecto real aquí, pero se deja por consistencia
)
study.optimize(objective, n_trials=N_TRIALS, show_progress_bar=True)

print("\n=== Mejores hiperparámetros (VALID) ===")
print(study.best_params)
print(f"Mejor RMSE valid: {study.best_value:.4f}")

# --------- Re-entrenar con los mejores params (train+valid) ---------
best_params = study.best_params.copy()
best_model = RandomForestRegressor(**best_params, random_state=SEED, n_jobs=-1)

best_model.fit(X_train_all, y_train_all)

# --------- Evaluación en TEST ---------
y_pred_test = best_model.predict(X_test)
mse  = mean_squared_error(y_test, y_pred_test)
rmse = mean_squared_error(y_test, y_pred_test)
mae  = mean_absolute_error(y_test, y_pred_test)
r2   = r2_score(y_test, y_pred_test)

print("\n=== Métricas en TEST ===")
print(f"MSE : {mse:,.2f}")
print(f"RMSE: {rmse:,.2f}")
print(f"MAE : {mae:,.2f}")
print(f"R²  : {r2:.4f}")


[I 2025-11-09 21:51:50,957] A new study created in memory with name: no-name-603c26c3-86db-426e-b8c4-1d444f52b993


Train: (692, 140), Valid: (172, 140), Test: (94, 140)


  0%|          | 0/60 [00:00<?, ?it/s]c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\sklearn\base.py:1365: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
Best trial: 0. Best value: 7.72287e+07:   2%|▏         | 1/60 [00:00<00:32,  1.83it/s]c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\sklearn\base.py:1365: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


[I 2025-11-09 21:51:51,506] Trial 0 finished with value: 77228746.58032861 and parameters: {'max_depth': 6, 'max_features': 'log2', 'bootstrap': True, 'n_estimators': 582, 'min_samples_split': 5, 'min_samples_leaf': 4, 'max_samples': 0.6521211214797689}. Best is trial 0 with value: 77228746.58032861.


Best trial: 1. Best value: 2.33128e+07:   3%|▎         | 2/60 [00:02<01:34,  1.63s/it]c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\sklearn\base.py:1365: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


...

[I 2025-11-09 21:54:38,000] Trial 57 finished with value: 570131179.9076813 and parameters: {'max_depth': None, 'max_features': 1.0, 'bootstrap': False, 'n_estimators': 1030, 'min_samples_split': 6, 'min_samples_leaf': 9}. Best is trial 45 with value: 19598476.052012965.


Best trial: 45. Best value: 1.95985e+07:  98%|█████████▊| 59/60 [02:48<00:03,  3.27s/it]c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\sklearn\base.py:1365: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


[I 2025-11-09 21:54:39,766] Trial 58 finished with value: 58303833.51420128 and parameters: {'max_depth': 24, 'max_features': 'sqrt', 'bootstrap': True, 'n_estimators': 1542, 'min_samples_split': 2, 'min_samples_leaf': 7, 'max_samples': 0.9765057871885373}. Best is trial 45 with value: 19598476.052012965.


Best trial: 45. Best value: 1.95985e+07: 100%|██████████| 60/60 [02:52<00:00,  2.87s/it]
c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\sklearn\base.py:1365: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


[I 2025-11-09 21:54:42,958] Trial 59 finished with value: 88469412.59344965 and parameters: {'max_depth': 10, 'max_features': 1.0, 'bootstrap': True, 'n_estimators': 1647, 'min_samples_split': 3, 'min_samples_leaf': 17, 'max_samples': 0.9163049595955386}. Best is trial 45 with value: 19598476.052012965.

=== Mejores hiperparámetros (VALID) ===
{'max_depth': 16, 'max_features': 1.0, 'bootstrap': True, 'n_estimators': 1183, 'min_samples_split': 2, 'min_samples_leaf': 2, 'max_samples': 0.8654367662002576}
Mejor RMSE valid: 19598476.0520

=== Métricas en TEST ===
MSE : 11,225,648.41
RMSE: 11,225,648.41
MAE : 2,629.43
R²  : 0.2921


In [96]:
"""El mejor modelo fue RFRegressor con los siguientes hiperparámetros:
    {'max_depth': 16, 'max_features': 1.0, 'bootstrap': True, 'n_estimators': 1183, 'min_samples_split': 2, 'min_samples_leaf': 2, 'max_samples': 0.8654367662002576}"""
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
#Entrenemos un modelo con esos hiperparámetros

best_model = RandomForestRegressor(
    n_estimators=1183,
    max_depth=16,
    max_features=1.0,
    bootstrap=True,
    min_samples_split=2,
    min_samples_leaf=2,
    max_samples=0.8654367662002576,
    random_state=42,
    n_jobs=-1
)
from sklearn.preprocessing import PowerTransformer
pt = PowerTransformer(method='yeo-johnson')
x_train_ready = pd.DataFrame(pt.fit_transform(x_train), columns=x_train.columns)
x_test_ready = pd.DataFrame(pt.transform(x_test), columns=x_test.columns)

best_model.fit(x_train_ready, y_train)
y_pred_test = best_model.predict(x_test_ready)
mse  = mean_squared_error(y_test, y_pred_test)
rmse = mean_squared_error(y_test, y_pred_test)
mae  = mean_absolute_error(y_test, y_pred_test)
r2   = r2_score(y_test, y_pred_test)
print("\n=== Métricas en TEST del mejor modelo entrenado manualmente ===")
print(f"MSE : {mse:,.2f}")
print(f"RMSE: {rmse:,.2f}")
print(f"MAE : {mae:,.2f}")
print(f"R²  : {r2:.4f}")


c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\sklearn\base.py:1365: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)



=== Métricas en TEST del mejor modelo entrenado manualmente ===
MSE : 11,223,523.16
RMSE: 11,223,523.16
MAE : 2,628.99
R²  : 0.2923


In [110]:
#quiero los valores 
print(feature_importances["feature"].tolist())

['Frio (Kw)', 'Frio_roll_mean_7_lag1', 'Sala Maq (Kw)', 'Envasado (Kw)', 'Frio_roll_mean_14_lag1', 'Servicios (Kw)', 'Prod Agua (Kw)', 'KW Gral Planta', 'Linea 2 (Kw)', 'CO 2 / Hl', 'EE Caldera / Hl', 'Cocina (Kw)', 'ET Linea 5/Hl', 'VAPOR DE LINEA 4 KG', 'Linea 3 (Kw)', 'Resto Serv (Kw)', 'Conversion Kg/Mj', 'Restos Planta (Kw)', 'Hl Cerveza L2', 'Frio_roll_mean_3_lag1']


In [97]:
feature_importances = best_model.feature_importances_
feature_names = x_train.columns
feature_importances = pd.DataFrame({'feature': feature_names, 'importance': feature_importances})
feature_importances = feature_importances.sort_values(by='importance', ascending=False)
feature_importances = feature_importances[:20]
print("Feature importances:")
print(feature_importances)
x_train = x_train[feature_importances['feature']]
x_test = x_test[feature_importances['feature']]

Feature importances:
                    feature  importance
76                Frio (Kw)    0.415853
134   Frio_roll_mean_7_lag1    0.140973
72            Sala Maq (Kw)    0.098940
67            Envasado (Kw)    0.063350
136  Frio_roll_mean_14_lag1    0.028401
71           Servicios (Kw)    0.012200
78           Prod Agua (Kw)    0.010649
81           KW Gral Planta    0.006070
68             Linea 2 (Kw)    0.005377
50                CO 2 / Hl    0.004458
13          EE Caldera / Hl    0.004136
66              Cocina (Kw)    0.003900
38            ET Linea 5/Hl    0.003631
109     VAPOR DE LINEA 4 KG    0.003530
69             Linea 3 (Kw)    0.003528
79          Resto Serv (Kw)    0.003396
98         Conversion Kg/Mj    0.003335
80       Restos Planta (Kw)    0.003300
59            Hl Cerveza L2    0.003267
132   Frio_roll_mean_3_lag1    0.003221


In [65]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
#Entrenemos un modelo con esos hiperparámetros

best_model = RandomForestRegressor(
    n_estimators=1183,
    max_depth=16,
    max_features=1.0,
    bootstrap=True,
    min_samples_split=2,
    min_samples_leaf=2,
    max_samples=0.8654367662002576,
    random_state=42,
    n_jobs=-1
)
from sklearn.preprocessing import PowerTransformer
pt = PowerTransformer(method='yeo-johnson')
x_train_ready = pd.DataFrame(pt.fit_transform(x_train), columns=x_train.columns)
x_test_ready = pd.DataFrame(pt.transform(x_test), columns=x_test.columns)

best_model.fit(x_train_ready, y_train)
y_pred_test = best_model.predict(x_test_ready)
mse  = mean_squared_error(y_test, y_pred_test)
rmse = mean_squared_error(y_test, y_pred_test)
mae  = mean_absolute_error(y_test, y_pred_test)
r2   = r2_score(y_test, y_pred_test)
print("\n=== Métricas en TEST del mejor modelo entrenado manualmente ===")
print(f"MSE : {mse:,.2f}")
print(f"RMSE: {rmse:,.2f}")
print(f"MAE : {mae:,.2f}")
print(f"R²  : {r2:.4f}")

c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\sklearn\base.py:1365: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)



=== Métricas en TEST del mejor modelo entrenado manualmente ===
MSE : 11,223,523.16
RMSE: 11,223,523.16
MAE : 2,628.99
R²  : 0.2923


In [17]:
# ==============================
# Optuna + Pruning para LGBM
# ==============================
import numpy as np
import pandas as pd
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from lightgbm import LGBMRegressor
import optuna
from optuna.samplers import TPESampler
from optuna.pruners import MedianPruner
from optuna.integration import LightGBMPruningCallback

SEED = 42
VAL_FRAC = 0.20   # último 20% del train como validación temporal
N_TRIALS = 50     # ajustá según tiempo disponible

# --------- Split temporal (train -> train/valid ; test queda intacto) ---------
X_train_all = x_train.copy()
y_train_all = y_train.copy()
X_test = x_test.copy()
y_test = y_test.copy()

n = len(X_train_all)
n_val = int(np.floor(n * VAL_FRAC))
n_tr = n - n_val
X_tr, y_tr = X_train_all.iloc[:n_tr], y_train_all[:n_tr]
X_val, y_val = X_train_all.iloc[n_tr:], y_train_all[n_tr:]

print(f"Train: {X_tr.shape}, Valid: {X_val.shape}, Test: {X_test.shape}")

# --------- Función objetivo para Optuna ---------
def objective(trial: optuna.Trial) -> float:
    # Espacio de búsqueda (razonable para baseline)
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 300, 2000),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.2, log=True),
        "num_leaves": trial.suggest_int("num_leaves", 31, 255),
        "max_depth": trial.suggest_int("max_depth", -1, 16),
        "min_child_samples": trial.suggest_int("min_child_samples", 5, 100),
        "subsample": trial.suggest_float("subsample", 0.6, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.6, 1.0),
        "reg_alpha": trial.suggest_float("reg_alpha", 1e-8, 10.0, log=True),
        "reg_lambda": trial.suggest_float("reg_lambda", 1e-8, 10.0, log=True),
        "random_state": SEED,
        "n_jobs": -1
    }

    # Modelo
    model = LGBMRegressor(**params)

    # Pruning callback: monitorea 'rmse' en el primer eval_set (valid_0)
    pruning_cb = LightGBMPruningCallback(trial, metric="rmse", valid_name="valid_0")

    # Entrena con early stopping y pruning
    model.fit(
        X_tr, y_tr,
        eval_set=[(X_val, y_val)],
        eval_metric="rmse",
        callbacks=[pruning_cb],
    )

    # Predicción en valid y métrica a minimizar (RMSE)
    y_pred_val = model.predict(X_val)
    rmse_val = mean_squared_error(y_val, y_pred_val)
    return rmse_val

# --------- Estudio Optuna ---------
study = optuna.create_study(
    direction="minimize",
    sampler=TPESampler(seed=SEED),
    pruner=MedianPruner(n_warmup_steps=10)
)
study.optimize(objective, n_trials=N_TRIALS, show_progress_bar=True)

print("\n=== Mejores hiperparámetros ===")
print(study.best_params)
print(f"Mejor RMSE valid: {study.best_value:.4f}")

# --------- Re-entrenar con los mejores params (train+valid) ---------
best_params = study.best_params.copy()
best_model = LGBMRegressor(**best_params, random_state=SEED, n_jobs=-1)

best_model.fit(
    X_train_all, y_train_all,
    eval_set=[(X_val, y_val)],  # opcional, solo para logging
    eval_metric="rmse",
)

# --------- Evaluación en TEST ---------
y_pred_test = best_model.predict(X_test)
mse = mean_squared_error(y_test, y_pred_test)
rmse = mean_squared_error(y_test, y_pred_test)
mae = mean_absolute_error(y_test, y_pred_test)
r2  = r2_score(y_test, y_pred_test)

print("\n=== Métricas en TEST ===")
print(f"MSE : {mse:,.2f}")
print(f"RMSE: {rmse:,.2f}")
print(f"MAE : {mae:,.2f}")
print(f"R²  : {r2:.4f}")


c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[I 2025-11-09 22:41:41,215] A new study created in memory with name: no-name-ab816747-189c-43b5-8fc0-6e4aefb7cbd0


Train: (692, 11), Valid: (172, 11), Test: (94, 11)


  0%|          | 0/50 [00:00<?, ?it/s]

[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000203 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2541
[LightGBM] [Info] Number of data points in the train set: 692, number of used features: 11
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Info] Start training from score 28710.196171
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with po

Best trial: 0. Best value: 3.46919e+08:   2%|▏         | 1/50 [00:00<00:17,  2.85it/s]

...

Best trial: 33. Best value: 2.04547e+07:  98%|█████████▊| 49/50 [00:23<00:00,  2.78it/s]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

Best trial: 33. Best value: 2.04547e+07: 100%|██████████| 50/50 [00:24<00:00,  2.07it/s]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

### Evaluación final del modelo
¿Vamos a aprobar? No lo sabemos. Para eso vamos a verificar que el modelo funcione dentro del rango de mae esperado para datos inéditos. Vamos a hacer pruebas con la variable inédita x_test y y_test

In [106]:
x_train

Frio (Kw)  Frio_roll_mean_7_lag1  Sala Maq (Kw)  Envasado (Kw)  \
0    24796.877744           24658.209509   28306.225915   14962.530183   
1    24796.877744           24658.209509   28306.225915   14962.530183   
2    28268.000000           26626.823553   31386.000000   14818.000000   
3    24246.000000           29890.189641   28070.000000   18696.000000   
4    29885.000000           28877.865079   33463.000000   14831.000000   
..            ...                    ...            ...            ...   
953  21756.666667           18942.571429   24529.333333   18948.333333   
954  23447.000000           19700.809524   26544.000000   18924.000000   
955  18856.000000           20144.666667   20656.000000    6233.000000   
956  10274.000000           19882.952381   10547.000000    1069.000000   
957  20679.000000           18387.380952   22366.000000   17463.000000   

     Frio_roll_mean_14_lag1  Servicios (Kw)  Prod Agua (Kw)  KW Gral Planta  \
0              26395.792079    40581.503049      673.820427    68820.020122   
1              26395.792079    40581.503049      673.820427    68820.020122   
2              65938.706722    42565.500000      943.000000    68039.000000   
3              29558.225590    39650.000000     1011.000000    69857.000000   
4              29282.342318    45385.000000     1018.000000    73431.000000   
..                      ...             ...             ...             ...   
953            18097.714286    37179.000000      275.666667    71860.666667   
954            18494.261905    38946.000000      258.000000    73678.000000   
955            18930.904762    31460.000000      234.000000    48969.000000   
956            18919.190476    16174.000000      155.000000    22264.000000   
957            18694.761905    33748.000000      276.000000    64588.000000   

     Linea 2 (Kw)  CO 2 / Hl  EE Caldera / Hl  Cocina (Kw)  ET Linea 5/Hl  \
0     4523.201387   0.448379         0.091459     1794.225      25.191172   
1     4523.201387   0.448379         0.091459     1794.225      25.191172   
2     1289.530000   0.689543         0.116571     1260.000       0.000000   
3     5861.350000   0.275763         0.073432     2020.000      13.010000   
4     5653.890000   0.541448         0.098328     1932.000      13.308435   
..            ...        ...              ...          ...            ...   
953   5642.080000   0.432624         0.013479     2486.000      50.319762   
954   5657.560000   0.251824         0.019722     2352.000      23.322541   
955   2517.310000   0.475733         0.067638     2066.000      28.178420   
956    449.940000   0.001687         0.063744     1029.000      51.836863   
957   5126.960000   0.031098         0.000000     2659.000      22.266000   

     VAPOR DE LINEA 4 KG  Linea 3 (Kw)  Resto Serv (Kw)  Conversion Kg/Mj  \
0           28918.129588   5540.002439      4991.821951          3.628813   
1           28918.129588   5540.002439      4991.821951          3.628813   
2           35280.450000   6629.000000      3302.500000          2.505079   
3           29736.150000   7115.000000      3998.000000          2.868745   
4           31668.900000   3732.000000      3782.000000          2.872046   
..                   ...           ...              ...               ...   
953         36217.610000   7812.000000      5471.333333          3.453020   
954         32355.800000   7835.000000      5727.000000          3.384492   
955         11386.050000   2315.000000      4975.000000          3.270637   
956          1422.720000    657.000000      1341.000000          3.816010   
957         35723.200000   7199.000000      4640.000000          3.462825   

     Restos Planta (Kw)  Hl Cerveza L2  Frio_roll_mean_3_lag1  
0           3747.276110    1470.268293           24631.518213  
1           3747.276110    1470.268293           24631.518213  
2           1864.340000      33.000000           26654.541620  
3           3058.290000    1348.000000           22182.333333  


In [107]:
x_test

Frio (Kw)  Frio_roll_mean_7_lag1  Sala Maq (Kw)  Envasado (Kw)  \
0      19199.0           18417.968635        19377.0        19390.0   
1      18576.0           18431.104643        19407.0        19677.0   
2      21478.0           18426.584193        24270.0        18937.0   
3      21039.0           20906.251934        24047.0         5579.0   
4      19832.0           18747.474876        22642.0          997.0   
..         ...                    ...            ...            ...   
225     9481.0           13061.000000         9793.0          452.0   
226    11587.0           11927.285714        11873.0         2758.0   
227    10123.0           11870.285714        10395.0         3339.0   
228    10360.0           11358.000000        10614.0         5513.0   
229    10568.0           11208.000000        10809.0         4306.0   

     Frio_roll_mean_14_lag1  Servicios (Kw)  Prod Agua (Kw)  KW Gral Planta  \
0              18510.400349         31245.0           103.0         63066.0   
1              18370.161874         30738.0           215.0         64958.0   
2              17460.300226         35599.0           438.0         68665.0   
3              20821.670503         33531.0           317.0         52300.0   
4              19728.716547         31383.0           224.0         42736.0   
..                      ...             ...             ...             ...   
225            14919.000000         16977.0            70.0         22953.0   
226            14353.000000         20821.0           105.0         31956.0   
227            13895.285714         18771.0            76.0         30480.0   
228            13407.285714         18461.0            83.0         32770.0   
229            12696.071429         18692.0            76.0         32119.0   

     Linea 2 (Kw)  CO 2 / Hl  EE Caldera / Hl  Cocina (Kw)  ET Linea 5/Hl  \
0     6275.150000   0.000171         0.000000        311.0      27.657067   
1     6493.090000   0.002616         0.000000       1345.0      24.108764   
2     5382.110000   0.368160         0.000000       2406.0      32.419244   
3     2522.420000   0.493976         0.000000       2352.0      32.893117   
4      673.470000   0.230394         0.000000       2227.0      44.659491   
..            ...        ...              ...          ...            ...   
225    461.300000   0.793820         0.178469        242.0      29.285922   
226   4351.070000   0.001906         0.068689       1387.0       3.325236   
227   5503.480000   0.000000         0.541538        313.0       0.000000   
228   6940.660156   1.020979         0.272386        235.0       5.850167   
229   6812.820312   1.355160         0.193186        251.0       0.373606   

     VAPOR DE LINEA 4 KG  Linea 3 (Kw)  Resto Serv (Kw)  Conversion Kg/Mj  \
0               34506.45        7692.0           4431.0          3.398585   
1               36541.05        7717.0           4041.0          3.517712   
2               36438.03        7938.0           4536.0          3.364916   
3                2450.00        3196.0           4505.0          3.435641   
4                1225.13         614.0           4322.0          3.027228   
..                   ...           ...              ...               ...   
225                 0.00         546.0           4487.0          8.316918   
226                 0.00         584.0           5086.0          6.579727   
227                 0.00         550.0           4900.0         10.935106   
228                 0.00        1287.0           4384.0          6.553919   
229                 0.00         528.0           4390.0          4.660586   

     Restos Planta (Kw)  Hl Cerveza L2  Frio_roll_mean_3_lag1  
0           5510.650000         3153.0           17922.625608  
1           6389.590000         2873.0           17874.421596  
2           4398.610000         1340.0           16645.983663  
3           3715.420000          364.0           19751.000000  
4           2655.970000          

In [134]:
#vamos a probar modelos de ML
#leamos x_train, y_train, x_test, y_test
import pandas as pd
x_train = pd.read_csv("x_train.csv")
y_train = pd.read_csv("y_train.csv")
x_test = pd.read_csv("x_val.csv")
y_test = pd.read_csv("y_val.csv")
"""El mejor modelo fue RFRegressor con los siguientes hiperparámetros:
    {'max_depth': 16, 'max_features': 1.0, 'bootstrap': True, 'n_estimators': 1183, 'min_samples_split': 2, 'min_samples_leaf': 2, 'max_samples': 0.8654367662002576}"""
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
#Entrenemos un modelo con esos hiperparámetros

best_model = RandomForestRegressor(
    n_estimators=1183,
    max_depth=16,
    max_features=1.0,
    bootstrap=True,
    min_samples_split=2,
    min_samples_leaf=2,
    max_samples=0.8654367662002576,
    random_state=42,
    n_jobs=-1
)
from sklearn.preprocessing import PowerTransformer
pt = PowerTransformer(method='yeo-johnson')
x_train_ready = pd.DataFrame(pt.fit_transform(x_train), columns=x_train.columns)
x_test_ready = pd.DataFrame(pt.transform(x_test), columns=x_test.columns)

best_model.fit(x_train_ready, y_train)
y_pred_test = best_model.predict(x_test_ready)
mse  = mean_squared_error(y_test, y_pred_test)
rmse = mean_squared_error(y_test, y_pred_test)
mae  = mean_absolute_error(y_test, y_pred_test)
r2   = r2_score(y_test, y_pred_test)
print("\n=== Métricas en TEST del mejor modelo entrenado manualmente ===")
print(f"MSE : {mse:,.2f}")
print(f"RMSE: {rmse:,.2f}")
print(f"MAE : {mae:,.2f}")
print(f"R²  : {r2:.4f}")
feature_importances = best_model.feature_importances_
feature_names = x_train.columns
feature_importances = pd.DataFrame({'feature': feature_names, 'importance': feature_importances})
feature_importances = feature_importances.sort_values(by='importance', ascending=False)
feature_importances = feature_importances[:20]
print("Feature importances:")
print(feature_importances)
x_train = x_train[feature_importances['feature']]
x_test = x_test[feature_importances['feature']]

c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\sklearn\base.py:1365: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)



=== Métricas en TEST del mejor modelo entrenado manualmente ===
MSE : 11,223,523.16
RMSE: 11,223,523.16
MAE : 2,628.99
R²  : 0.2923
Feature importances:
                    feature  importance
76                Frio (Kw)    0.415853
134   Frio_roll_mean_7_lag1    0.140973
72            Sala Maq (Kw)    0.098940
67            Envasado (Kw)    0.063350
136  Frio_roll_mean_14_lag1    0.028401
71           Servicios (Kw)    0.012200
78           Prod Agua (Kw)    0.010649
81           KW Gral Planta    0.006070
68             Linea 2 (Kw)    0.005377
50                CO 2 / Hl    0.004458
13          EE Caldera / Hl    0.004136
66              Cocina (Kw)    0.003900
38            ET Linea 5/Hl    0.003631
109     VAPOR DE LINEA 4 KG    0.003530
69             Linea 3 (Kw)    0.003528
79          Resto Serv (Kw)    0.003396
98         Conversion Kg/Mj    0.003335
80       Restos Planta (Kw)    0.003300
59            Hl Cerveza L2    0.003267
132   Frio_roll_mean_3_lag1    0.003221


In [135]:
x_val = x_test.copy()
y_val = y_test.copy()

In [136]:
import numpy as np
import pandas as pd

# =========================
# 1) Redefinir train y leer test
# =========================
x_train = pd.concat([x_train, x_val], ignore_index=True)
y_train = pd.concat([y_train, y_val], ignore_index=True)

x_test  = pd.read_csv("X_test.csv")
y_test  = pd.read_csv("y_test.csv")

# Aseguramos mismas columnas y orden
x_test = x_test[x_train.columns]

# =========================
# 2) Columnas numéricas / no numéricas
# =========================
numeric_cols = x_train.select_dtypes(include=[np.number]).columns.tolist()
other_cols   = [c for c in x_train.columns if c not in numeric_cols]

# Copias aisladas de numéricas
Xtr_num = x_train[numeric_cols].copy()
Xte_num = x_test[numeric_cols].copy()

# =========================
# 3) Límites por feature con MAD (fallback a percentiles si MAD=0)
# =========================
def mad_bounds(col_train: pd.Series, Z: float = 3.5,
               q_low: float = 0.001, q_high: float = 0.999):
    """
    Devuelve (low, high) por MAD; si MAD==0, usa percentiles (q_low, q_high).
    """
    med = col_train.median()
    mad = np.median(np.abs(col_train - med))
    if mad > 0:
        # robust z-score bounds
        # 0.6745 hace que MAD sea comparable a sigma para Normal
        scale = 0.6745 * (col_train - med).abs().median() / mad  # opcional; muchos usan 0.6745 directamente
        # usamos la forma clásica: robust_z = 0.6745*(x-med)/MAD
        # límites: med ± Z * MAD / 0.6745
        low  = med - (Z * mad / 0.6745)
        high = med + (Z * mad / 0.6745)
    else:
        # Sin dispersión: usamos percentiles amplios
        low  = col_train.quantile(q_low)
        high = col_train.quantile(q_high)
        if low == high:
            # todos iguales: expandir un poco para no anular la feature
            low, high = low - 1e-12, high + 1e-12
    return low, high

bounds = {}
for c in numeric_cols:
    low, high = mad_bounds(Xtr_num[c].dropna(), Z=3.5, q_low=0.001, q_high=0.999)
    bounds[c] = (low, high)

# =========================
# 4) Reemplazo cellwise: fuera de [low, high] -> np.nan
#    (usamos límites aprendidos SOLO del train)
# =========================
def mask_outliers_to_nan(df_num: pd.DataFrame, bounds_dict: dict) -> pd.DataFrame:
    df = df_num.copy()
    for c, (low, high) in bounds_dict.items():
        mask_low  = df[c] < low
        mask_high = df[c] > high
        df.loc[mask_low | mask_high, c] = np.nan
    return df

Xtr_num_nan = mask_outliers_to_nan(Xtr_num, bounds)
Xte_num_nan = mask_outliers_to_nan(Xte_num, bounds)

# Si querés contar cuántas celdas se “nanearon”:
tr_nan_cells = Xtr_num_nan.isna().sum().sum() - Xtr_num.isna().sum().sum()
te_nan_cells = Xte_num_nan.isna().sum().sum() - Xte_num.isna().sum().sum()
print(f"Celdas convertidas a NaN por outliers - train: {tr_nan_cells}, test: {te_nan_cells}")

# =========================
# 5) Imputación KNN en ESPACIO ESCALADO y volver a original
# =========================
from sklearn.preprocessing import RobustScaler
from sklearn.impute import KNNImputer

scaler = RobustScaler()
Xtr_scaled = pd.DataFrame(scaler.fit_transform(Xtr_num_nan), columns=numeric_cols, index=Xtr_num_nan.index)
Xte_scaled = pd.DataFrame(scaler.transform(Xte_num_nan),    columns=numeric_cols, index=Xte_num_nan.index)

imputer = KNNImputer(n_neighbors=5, weights='distance')
Xtr_imp_scaled = pd.DataFrame(imputer.fit_transform(Xtr_scaled), columns=numeric_cols, index=Xtr_scaled.index)
Xte_imp_scaled = pd.DataFrame(imputer.transform(Xte_scaled),    columns=numeric_cols, index=Xte_scaled.index)

# Volvemos a la escala original
Xtr_imp = pd.DataFrame(scaler.inverse_transform(Xtr_imp_scaled), columns=numeric_cols, index=Xtr_imp_scaled.index)
Xte_imp = pd.DataFrame(scaler.inverse_transform(Xte_imp_scaled), columns=numeric_cols, index=Xte_imp_scaled.index)

# =========================
# 6) Reconstruir datasets finales
# =========================
x_train_clean = pd.concat([Xtr_imp, x_train[other_cols].reset_index(drop=True)], axis=1)[x_train.columns]
x_test_clean  = pd.concat([Xte_imp, x_test[other_cols].reset_index(drop=True)],  axis=1)[x_test.columns]

# Resultado final para modelar
x_train = x_train_clean
x_test  = x_test_clean


Celdas convertidas a NaN por outliers - train: 686, test: 206


In [137]:
best_model = RandomForestRegressor(
    n_estimators=1183,
    max_depth=16,
    max_features=1.0,
    bootstrap=True,
    min_samples_split=2,
    min_samples_leaf=2,
    max_samples=0.8654367662002576,
    random_state=42,
    n_jobs=-1
)
from sklearn.preprocessing import PowerTransformer
pt = PowerTransformer(method='yeo-johnson')
x_train_ready = pd.DataFrame(pt.fit_transform(x_train), columns=x_train.columns)
x_test_ready = pd.DataFrame(pt.transform(x_test), columns=x_test.columns)

best_model.fit(x_train_ready, y_train)
y_pred_test = best_model.predict(x_test_ready)
mse  = mean_squared_error(y_test, y_pred_test)
rmse = mean_squared_error(y_test, y_pred_test)
mae  = mean_absolute_error(y_test, y_pred_test)
r2   = r2_score(y_test, y_pred_test)
print("\n=== Métricas en TEST del mejor modelo entrenado manualmente ===")
print(f"MSE : {mse:,.2f}")
print(f"RMSE: {rmse:,.2f}")
print(f"MAE : {mae:,.2f}")
print(f"R²  : {r2:.4f}")


c:\Users\agusm\Trabajo-Final-Lab-Datos-\.venv\Lib\site-packages\sklearn\base.py:1365: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)



=== Métricas en TEST del mejor modelo entrenado manualmente ===
MSE : 12,165,506.70
RMSE: 12,165,506.70
MAE : 2,630.52
R²  : 0.6108
